In [18]:
from math import pi
from ngsolve import *
from ngsolve.webgui import Draw
from netgen.occ import *
from netgen.geom2d import SplineGeometry

impose_3d = 1 # Impose 3D on the 2 mesh


# Geometry definition of a circle in a circle
#---------------------------------------------
outer = Circle((0,0), 1.4).Face()
outer.edges.name = 'outerbnd'
inner = Circle((0,0), 1).Face()
inner.edges.name = 'innerbnd'
inner.faces.name ='inner'
pmlregion = outer - inner
pmlregion.faces.name = 'pmlregion'

if impose_3d:
    geo = OCCGeometry(Glue([inner, pmlregion]), dim=3)
else:
    geo = OCCGeometry(Glue([inner, pmlregion]), dim=2)

mesh = Mesh(geo.GenerateMesh (maxh=0.05))
mesh.Curve(3)
Draw(mesh);


# PML defintion
#--------------
mesh.SetPML(pml.Radial(rad=1,alpha=0.5j,origin=(0,0)), "pmlregion")

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

In [21]:
# Basic constants
#----------------

mu0 = 4*pi*1e-7
eps0 = 8.854e-12
mu = CoefficientFunction((mu0))
eps = CoefficientFunction((eps0))

# Maxwell caracteristics
#-----------------------
freq=3000e6 #1000 MHz
om=2*pi*freq
k0=om*sqrt(mu0*eps0)
lambda0 = 2*pi/k0
print("k0=",k0)
print("lambda0=",lambda0)

if impose_3d:
    f = CoefficientFunction(((0,1e11*exp(-(200**2)*((x-0)*(x-0) + (y-0)*(y-0))**2), 0)))
else:
    f = CoefficientFunction(((0,1e11*exp(-(200**2)*((x-0)*(x-0) + (y-0)*(y-0))**2))))

Draw(f, mesh, "uin",min=-1, max=1, animate_complex=True)

k0= 62.8746837898545
lambda0= 0.0999318792310721


WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene

In [22]:
# Impose bilinear and linear forms
#----------------------------------
order = 5 # mesh order
fes = HCurl(mesh, complex=True, order=order, dirichlet="scat")
u = fes.TrialFunction()
v = fes.TestFunction()

uscat = GridFunction (fes)

a = BilinearForm(fes, symmetric=True)
a += SymbolicBFI((1/mu)*curl(u)*curl(v) - om**2*(eps*u)*v)
a += SymbolicBFI(-1j * k0 * u.Trace() * v.Trace(), BND)

b = LinearForm(f * v * dx)

a.Assemble()
b.Assemble()

res = uscat.vec.CreateVector()
res.data = b.vec - a.mat * uscat.vec
uscat.vec.data += a.mat.Inverse(freedofs=fes.FreeDofs(), inverse="sparsecholesky") * res

#Draw(f, mesh, min=-1, max=1, order=3, animate_complex=True);
Draw(uscat, mesh, min=-1, max=1, order=order, animate_complex=True);
Draw(uscat, mesh, order = order, animate_complex=True);

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {'Complex': {'phase': 0.0, 'sp…

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {'Complex': {'phase': 0.0, 'sp…

In [23]:

Draw(uscat, mesh, min=-1, max=1, order=3, animate_complex=True);
Draw(uscat, order = 3, animate_complex=True);

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {'Complex': {'phase': 0.0, 'sp…

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {'Complex': {'phase': 0.0, 'sp…